In [1]:
import geopandas as gpd
import matplotlib.pyplot as plt
import json
import plotly.express as px
import pandas as pd
import folium
import streamlit as st
import folium
from streamlit_folium import st_folium
from shapely.geometry import box
# pd.set_option('display.max_rows', None)

## TEST VIZ ENJEU MAP

In [22]:
file_path = "CartePotentielEolien_2023.gpkg"
gdf = gpd.read_file(file_path)

c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\pyogrio\raw.py:196: RuntimeWarning: Field format 'character varying(256)' not supported
  return ogr_read(
c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\pyogrio\raw.py:196: RuntimeWarning: Field format 'character varying(30)' not supported
  return ogr_read(
c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\pyogrio\raw.py:196: RuntimeWarning: Field format 'character varying' not supported
  return ogr_read(
c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\pyogrio\raw.py:196: RuntimeWarning: Field format 'timestamp with time zone' not supported
  return ogr_read(
c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\pyogrio\geopandas.py:261: UserWarning: More than one layer found in 'CartePotentielEolien_2023.gpkg': 'CartePotentielEolien_2023' (default), 'layer_styles'. Specify layer parameter to avoid this warning.
  result = read_func(


In [27]:
gdf.head()

ID CODE_ENJEU                   DOMAIN_ENJ                 NATURE_ENJ  \
0  1272          1  contrainte_civile_militaire       perimetre_champs_tir   
1  1273          1             activite_humaine  perimetre_habitation_250m   
2  1274          1             activite_humaine  perimetre_habitation_250m   
3  1275          1             activite_humaine  perimetre_habitation_250m   
4  1276          1             activite_humaine  perimetre_habitation_250m   

  MILLESIME   REGION                                           geometry  
0      2023  REUNION  MULTIPOLYGON (((55.6115 -21.17697, 55.61152 -2...  
1      2023  REUNION  MULTIPOLYGON (((55.70136 -21.37655, 55.70134 -...  
2      2023  REUNION  MULTIPOLYGON (((55.40712 -21.30632, 55.40701 -...  
3      2023  REUNION  MULTIPOLYGON (((55.33164 -21.26079, 55.33165 -...  
4      2023  REUNION  MULTIPOLYGON (((55.36081 -21.22004, 55.36087 -...

In [34]:
gdf2 = gdf[gdf['CODE_ENJEU'] != '0_petit_eolien']
gdf2['CODE_ENJEU'] = gdf2['CODE_ENJEU'].astype(int)
gdf2['REGION'].value_counts()

c:\Users\j3r3m\miniconda3\envs\final_project\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


REGION
GUYANE                        465
REUNION                       255
AUVERGNE RHONE ALPES          109
MARTINIQUE                    105
PROVENCE ALPES COTE D’AZUR     94
OCCITANIE                      90
NOUVELLE AQUITAINE             86
GRAND EST                      86
NORMANDIE                      81
PAYS DE LA LOIRE               74
HAUTS DE FRANCE                72
CENTRE VAL DE LOIRE            71
BRETAGNE                       69
CORSE                          53
GUADELOUPE                     48
ILE DE FRANCE                  43
BOURGOGNE FRANCHE COMTE         4
Name: count, dtype: int64

In [35]:
# gdf2 = gdf2[(gdf2['CODE_ENJEU'] == 0) | (gdf2['CODE_ENJEU'] == 1)]
# gdf2['CODE_ENJEU'] = 0
# gdf2 = gdf2[(gdf2['CODE_ENJEU'] == 2)]


# metropolitan_regions = ['HAUTS DE FRANCE', 'ILE DE FRANCE', 'NORMANDIE', 'NOUVELLE AQUITAINE',
#     'OCCITANIE', 'PAYS DE LA LOIRE', 'PROVENCE ALPES COTE D’AZUR', 'AUVERGNE RHONE ALPES', 
#     'PROVENCE ALPES COTE D’AZUR', 'GRAND EST', 'CENTRE VAL DE LOIRE', 'BOURGOGNE FRANCHE COMTE',
#     'CORSE', 'BRETAGNE'
# ]
metropolitan_regions = ['BOURGOGNE FRANCHE COMTE']


# Filter the DataFrame to keep only metropolitan regions
gdf2 = gdf2[gdf2['REGION'].isin(metropolitan_regions)]
columns_to_keep = ['region', 'enjeu', 'geometry']
gdf2.rename(columns={'CODE_ENJEU': 'enjeu', 'REGION' : 'region'}, inplace=True)
gdf2 = gdf2[columns_to_keep]
gdf2.reset_index(drop=True, inplace=True)
# indices_to_remove = [
#     12, 192, 68, 65, 264, 101, 137, 242 , 100, 169, 144, 242 
# ]
# try: 
#     gdf2 = gdf2.drop(indices_to_remove)
# except:
#     print("continue")


# print(len(gdf2))
# tolerance = 0.9
# gdf2['geometry'] = gdf2['geometry'].apply(lambda geom: geom.simplify(tolerance=tolerance, preserve_topology=True))




In [5]:
merged_gdf = gdf2.dissolve()
merged_gdf


In [ ]:
total_area = gdf2.total_bounds
total_geometry = gpd.GeoSeries(box(total_area[0], total_area[1], total_area[2], total_area[3]), crs=gdf.crs)
authorized_geometry = total_geometry.difference(merged_gdf.geometry.unary_union)
enjeu_3_gdf = gpd.GeoDataFrame({'region': ['Authorized Area'], 'enjeu': [3], 'geometry': authorized_geometry}, crs=gdf.crs)
enjeu_3_gdf


C:\Users\j3r3m\AppData\Local\Temp\ipykernel_12380\3887831523.py:3: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  authorized_geometry = total_geometry.difference(merged_gdf.geometry.unary_union)


region  enjeu                                           geometry
0  Authorized Area      3  MULTIPOLYGON (((7.18556 44.11549, 5.49447 44.1...

In [8]:
# merged_gdf = gdf2.dissolve(by=['region'])
# merged_gdf = merged_gdf.reset_index()
# merged_gdf

C:\Users\j3r3m\AppData\Local\Temp\ipykernel_12380\9633163.py:2: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  authorized_geometry = total_geometry.difference(merged_gdf.geometry.unary_union)


region  enjeu                                           geometry
0  Authorized Area      3  MULTIPOLYGON (((3.53526 48.12008, 2.66444 48.1...

In [36]:
gdf2.to_file("gdf2_BFC.gpkg", driver="GPKG")


In [4]:
file_path = "app/gdf2_BFC.gpkg"
gdf2 = gpd.read_file(file_path)
gdf2.head()

region  enjeu  \
0  BOURGOGNE FRANCHE COMTE      1   
1  BOURGOGNE FRANCHE COMTE      0   
2  BOURGOGNE FRANCHE COMTE      2   
3  BOURGOGNE FRANCHE COMTE      3   

                                            geometry  
0  MULTIPOLYGON (((3.74082 46.54021, 3.73911 46.5...  
1  MULTIPOLYGON (((5.49361 47.31195, 5.49444 47.3...  
2  MULTIPOLYGON (((6.0406 46.39787, 6.04061 46.39...  
3  MULTIPOLYGON (((6.2229 46.66322, 6.24521 46.66...

In [5]:
# Define the latitude and longitude for the map's initial location
latitude = 47.98199
longitude = 0.1133009

enjeu_order = [3, 2, 1, 0]


m = folium.Map(location=[latitude, longitude], zoom_start=7)  # Adjust zoom_start as needed
    
# Loop through each unique 'enjeu' value
for enjeu_value in enjeu_order:
    # Filter the GeoDataFrame for the current 'enjeu' value
    enjeu_gdf = gdf2[gdf2['enjeu'] == enjeu_value]

    if enjeu_value == 0:
            # Directly use the style function inside the folium.GeoJson call
        folium.GeoJson(
            enjeu_gdf,
            style_function=lambda feature: {
                'fillColor': 'white',  # Set all features to blue
                'color': 'white',     # Outline color
                'weight': 0,          # Outline thickness
                'fillOpacity': 1    # Fill opacity
            },
            name=f'Enjeu {enjeu_value}'
        ).add_to(m)
    elif enjeu_value == 1:
        # Directly use the style function inside the folium.GeoJson call
        folium.GeoJson(
            enjeu_gdf,
            style_function=lambda feature: {
                'fillColor': '#FECDFF',  # Set all features to blue
                'color': 'white',     # Outline color
                'weight': 0,          # Outline thickness
                'fillOpacity': 1    # Fill opacity
            },
            name=f'Enjeu {enjeu_value}'
        ).add_to(m)

    elif enjeu_value == 2:
            # Directly use the style function inside the folium.GeoJson call
        folium.GeoJson(
            enjeu_gdf,
            style_function=lambda feature: {
                'fillColor': '#D086FF',  # Set all features to blue
                'color': 'white',     # Outline color
                'weight': 0,          # Outline thickness
                'fillOpacity': 1    # Fill opacity
            },
            name=f'Enjeu {enjeu_value}'
        ).add_to(m)
    elif enjeu_value == 3:
            # Directly use the style function inside the folium.GeoJson call
        folium.GeoJson(
            enjeu_gdf,
            style_function=lambda feature: {
                'fillColor': '#810179',  # Set all features to blue
                'color': 'white',     # Outline color
                'weight': 0,          # Outline thickness
                'fillOpacity': 1    # Fill opacity
            },
            name=f'Enjeu {enjeu_value}'
        ).add_to(m)


folium.LayerControl().add_to(m)
print(f'Saving....')
# Save the map to an HTML file named after the region
m.save(f'map_Corse.html')
print(f'Saving Done')


# # Display the Folium map in the Streamlit app
# st.title('Folium Map in Streamlit')
# st_folium(m, width=700, height=500)


Saving....
Saving Done


## TEST HEATMAP FOR WIND SPEED AND WIND DIRECTION

In [6]:
import geopandas as gpd
import matplotlib.pyplot as plt
import json
import plotly.express as px
import pandas as pd
import folium
import streamlit as st
import folium
from streamlit_folium import st_folium
from shapely.geometry import box
# pd.set_option('display.max_rows', None)
from folium.plugins import HeatMap, TimestampedGeoJson, HeatMapWithTime
import branca.colormap as cm
import numpy as np


In [11]:
df = pd.read_csv('app/datameteo_france_1950-2022_clean_02.csv')
df.head()


# Filter the DataFrame for the specific Year and Month
df_filtered = df[(df['Year'] == 2012) & (df['Month'] == 1)]

# Create a map centered around the mean latitude and longitude of the filtered DataFrame
map_center = [df_filtered['LAT'].mean(), df_filtered['LON'].mean()]
mymap = folium.Map(location=map_center, zoom_start=4)

# Prepare data for the HeatMap (latitude, longitude, and wind speed as intensity)
heat_data = [[row['LAT'], row['LON'], row['vent_speed_inst_moy_mensu']] for index, row in df_filtered.iterrows()]

# Define the colormap
colormap = cm.LinearColormap(colors=['#5F97CF', '#90E1A9', '#F4EB87', '#FFD391', '#D85356'], 
                             vmin=min(df_filtered['vent_speed_inst_moy_mensu']), 
                             vmax=max(df_filtered['vent_speed_inst_moy_mensu']))


# radius: Reduces the size of each data point. Smaller radius limits the overlap of color intensity.
# blur: Controls how much the color intensity of each point spreads out. Lower blur values can help reduce the excessive blending of colors.

heatmap_group = folium.FeatureGroup(name='Wind Speed Heatmap', overlay=True, show=True)

# Adjust HeatMap parameters
HeatMap(
    heat_data,
    min_opacity=0.01,  # Set lower opacity to reduce intensity
    max_val=max(df_filtered['vent_speed_inst_moy_mensu']),
    radius=20,  # Reduce radius to lessen the overlap when zooming out
    blur=10,  # Reduce blur for better definition
).add_to(heatmap_group)



# Add the colormap (color scale) to the map
colormap.caption = 'Wind Speed (m/s)'
colormap.add_to(mymap)


heatmap_group.add_to(mymap)


wind_direction_group = folium.FeatureGroup(name='Wind Direction', overlay=True, show=False)


for idx, row in df_filtered.iterrows():
    wind_direction = row['vent_dir_inst']
    
    # Unique animation name for each arrow
    animation_name = f"moveAndRotate_{idx}"
    
    # Customize these values to adjust animation
    duration = "1s"  # Change to control speed (e.g., "1s", "3s")
    amplitude = 6  # Distance the arrow moves, change as needed
    timing_function = "ease-in-out"  # Options: linear, ease, ease-in, ease-out, ease-in-out

    # Generate unique keyframes animation
    icon_html = f"""
    <div style="
        font-size: 15px;
        color: #183153;
        position: relative;
        display: flex;
        justify-content: center;
        align-items: center;
        width: 15px;
        height: 15px;
        animation: {animation_name} {duration} infinite alternate {timing_function};
    ">
        &rarr;
</div>
    <style>
        @keyframes {animation_name} {{
            0% {{ transform: translate(0, 0) rotate({wind_direction}deg); }}
            100% {{ transform: translate({amplitude * np.cos(np.radians(wind_direction))}px, {amplitude * np.sin(np.radians(wind_direction))}px) rotate({wind_direction}deg); }}
        }}
    </style>
    """
    folium.Marker(
        location=[row['LAT'], row['LON']],
        icon=folium.DivIcon(html=icon_html),
        tooltip=f"Wind Speed: {row['vent_speed_inst_moy_mensu']} m/s"
    ).add_to(wind_direction_group)


wind_direction_group.add_to(mymap)

folium.LayerControl().add_to(mymap)

# Display the map
mymap

C:\Users\j3r3m\AppData\Local\Temp\ipykernel_14372\1253656001.py:27: UserWarning: The `max_val` parameter is no longer necessary. The largest intensity is calculated automatically.
  HeatMap(


## TIMELINE WITH TimestampedGeoJson

In [8]:
import folium
from folium import plugins
import numpy as np
import pandas as pd
from datetime import datetime

# Load your data
df = pd.read_csv('app/datameteo_france_1950-2022_clean_02.csv')

# Filter the DataFrame for the specific Year
df_filtered = df[df['Year'] == 2012]

# Create a map centered around the mean latitude and longitude of the filtered DataFrame
map_center = [df_filtered['LAT'].mean(), df_filtered['LON'].mean()]
mymap = folium.Map(location=map_center, zoom_start=5)

# Define the colormap
colormap = cm.LinearColormap(colors=['#5F97CF', '#90E1A9', '#F4EB87', '#FFD391', '#D85356'], 
                             vmin=min(df_filtered['vent_speed_inst_moy_mensu']), 
                             vmax=max(df_filtered['vent_speed_inst_moy_mensu']))

# Prepare data for the timeline
timeline_data = []

for _, row in df_filtered.iterrows():
    feature = {
        "type": "Feature",
        "geometry": {
            "type": "Point",
            "coordinates": [row['LON'], row['LAT']]
        },
        "properties": {
            "time": str(datetime(row['Year'], row['Month'], 1)),
            "style": {
                "color": colormap(row['vent_speed_inst_moy_mensu']),
                "icon": "circle",
                "iconstyle": {
                    "fillColor": colormap(row['vent_speed_inst_moy_mensu']),
                    "fillOpacity": 0.2,
                    "stroke": "true",
                    "radius": 0  # You can adjust this size based on the intensity if needed
                }
            },
            "popup": f"Wind Speed: {row['vent_speed_inst_moy_mensu']} m/s",
            "icon": "circle"
        }
    }
    timeline_data.append(feature)

# Add the timeline to the map
plugins.TimestampedGeoJson(
    {
        "type": "FeatureCollection",
        "features": timeline_data
    },
    period="P1M",  # Adjust period to fit your data granularity
    add_last_point=True,
    auto_play=False,
    loop=True,
    max_speed=1,
    loop_button=True,
    date_options='YYYY-MM-DD',
    time_slider_drag_update=True
).add_to(mymap)

# Add the colormap (color scale) to the map
colormap.caption = 'Wind Speed (m/s)'
colormap.add_to(mymap)

# Add layer control
folium.LayerControl().add_to(mymap)

# Display the map
mymap


## TIMELINE WITH HeatMapWithTime

In [9]:
df = pd.read_csv('app/datameteo_france_1950-2022_clean_02.csv')
df.head()


# Filter the DataFrame for the specific Year and Month
df_filtered = df[(df['Year'] == 2012)]
df_filtered['Date'] = pd.to_datetime(df_filtered[['Year', 'Month']].assign(DAY=1))
df_filtered

# # Group data by time and create a list of heatmap data for each time
heatmap_data = []
time_index = df_filtered['Date'].sort_values().unique()
for time_point in time_index:
    data_at_time = df_filtered[df_filtered['Date'] == time_point]
    heatmap_data.append(data_at_time[['LAT', 'LON', 'vent_speed_inst_moy_mensu']].values.tolist())

# Create the Folium map
mymap = folium.Map(location=[df_filtered['LAT'].mean(), df_filtered['LON'].mean()], zoom_start=6)

# Define the colormap
colormap = cm.LinearColormap(colors=['#5F97CF', '#90E1A9', '#F4EB87', '#FFD391', '#D85356'], 
                             vmin=min(df_filtered['vent_speed_inst_moy_mensu']), 
                             vmax=max(df_filtered['vent_speed_inst_moy_mensu']))

# Create a custom timeline index, labeling forecasted data differently
timeline_labels = []
for time_point in time_index:
    if time_point < pd.to_datetime('2012-06-01'):
        timeline_labels.append(time_point.strftime('Historical %Y-%m-%d'))
    else:
        timeline_labels.append(time_point.strftime('Forecast %Y-%m-%d'))


# Add the heatmap with time
HeatMapWithTime(
    name='Wind Speed Forecast',  # Naming the layer
    index=timeline_labels,  # Use the custom timeline labels
    data=heatmap_data,
    auto_play=True,
    max_opacity=0.8,
    radius=10,
    use_local_extrema=True
).add_to(mymap)


# Add the colormap (color scale) to the map
colormap.caption = 'Wind Speed (m/s)'
colormap.add_to(mymap)

folium.LayerControl().add_to(mymap)

mymap

C:\Users\j3r3m\AppData\Local\Temp\ipykernel_14372\955321535.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_filtered['Date'] = pd.to_datetime(df_filtered[['Year', 'Month']].assign(DAY=1))
